In [1]:
%matplotlib osx 

import numpy as np
from numpy.random import rand
from landscapeWithOcean import LandscapeWithOcean 

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm
from matplotlib.animation import FFMpegWriter

In [2]:
def Randomize(Z,NX,NY):
    for x in range(NX):
        for y in range(NY):
            Z[x,y] = np.random.rand()
            
    return Z

In [3]:
# Copied from my 2-D Perlin file

N = 50
SquareSize = 10

# define ease curve function

def ease(t):
    return 6*t**5-15*t**4+10*t**3

# create gradient vector basis

gradientArray = np.ndarray(shape=(SquareSize + 1, SquareSize + 1, 2))

# def generateRandGradientVec():
#     angle = np.random.rand() * 2 * np.pi
#     x = np.cos(angle)
#     y = np.sin(angle)
#     return np.array([x, y])
    
def generateRandGradientVec():
    angle = np.ceil(4 * np.random.rand()) * np.pi / 2
    x = np.cos(angle)
    y = np.sin(angle)
    return np.array([x, y])

for i in range(SquareSize + 1):
    for j in range(SquareSize + 1):
        gradientArray[i, j] = generateRandGradientVec()
        

def MyPerlin(i, j):
    x = i + 0.005
    y = j + 0.005
    
    LeftX = (((i * 50) // 10) * 10 ) / 50
    RightX = ((((i * 50) // 10) + 1) * 10) / 50
    
    BotY = (((j * 50) // 10) * 10) / 50
    TopY = ((((j * 50) // 10) + 1) * 10) / 50
    
    currPos = np.array([x, y])
    
    BotLeftVec = currPos - np.array([LeftX, BotY])
    TopLeftVec = currPos - np.array([LeftX, TopY])
    TopRightVec = currPos - np.array([RightX, TopY])
    BotRightVec = currPos - np.array([RightX, BotY])
    
    
    l = int(LeftX * 50//10)
    r = int(RightX * 50//10)
    b = int(BotY * 50//10)
    t = int(TopY * 50//10)
    
    BotLeftGrad = gradientArray[l, b]
    TopLeftGrad = gradientArray[l, t]
    TopRightGrad = gradientArray[r, t]
    BotRightGrad = gradientArray[r, b]
        
    dot1 = np.dot(BotLeftGrad, BotLeftVec)
    dot2 = np.dot(TopLeftGrad, TopLeftVec)
    dot3 = np.dot(TopRightGrad, TopRightVec)
    dot4 = np.dot(BotRightGrad, BotRightVec)
    
    topInterp = dot2 + ease(((x * 50) - (l * 10))/10)*(dot3 - dot2)
    botInterp = dot1 + ease(((x * 50) - (l * 10))/10)*(dot4 - dot1)
    
    ret = botInterp + ease(((y * 50) - (b * 10))/10)*(topInterp - botInterp)
    
    return ret

In [4]:
### Define simulation grid and initial conditions

NX = 50 #number of rows
NY = 50 #number of columns

d  = 5 # grid spacing in meters
dx = d # keep dx=dy for simplicity
dy = d

LX=NX*dx
LY=NY*dy

Z = rand(NX,NY)*0.1
Z2 = rand(NX, NY)*0.1
Z = Randomize(Z,NX,NY)
for i in range(NX):
    for j in range(NY):
        Z2[i, j] = (MyPerlin(i/N, j/N) + 0.1)*5
        
x = np.arange(NX)
y = np.arange(NY)
X,Y = np.meshgrid(y,x) 
ZMaxOrg = np.max(Z)

# fig = plt.figure(dpi=200)
# ax = fig.gca(projection='3d')
# ax.plot_surface(X, Y, Z, cmap=cm.coolwarm, antialiased=True)
# ax.set_aspect("auto")
# ax.view_init(60, -45)
# plt.draw()

In [5]:
### Physical Parameters

# For part 3, multiplying by 1000 for K, keeping D constant
K = 1000 * 1.0e-6 # meters^(1-2m)/yr
D = 0.005 # m^2/yr

# uplift rate
# uplift = 0.03 / 600.
uplift = 0.0

In [6]:
### Model parameters

# Time step
dt = d**2 / D / 8. 
#dt = d**2 / D /16. #extra small steps 
print(' dt[years] = ',dt)

#Area exponent A^m, default m=1, changing to 2 for part 3
m=2

#gradient exponent g^n, default n=1, changng to 1000 for part 3
n=1000

#erosion threshold 
theta_c = 10 

 dt[years] =  625.0


In [7]:
# Total simulation time
T = 30.0 * 625.0

# total number of iterations
n_iter = int(np.round(T/dt))
print('Number of interation: ',n_iter)

Number of interation:  30


In [8]:
# Initialize landscape 
ls = LandscapeWithOcean(NX,NY)

# Keeping it constant at 0.1 for part 3
oceanLevelParameter=0.1  # what does this parameter do?
# answered below

ls.ComputeOceanVolumeFromOceanLevelParameter(Z,NX,NY,oceanLevelParameter)

ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))

Minimum elevation           0.000270661422545615
Maximum elevation           0.9993772925428772
Beach level                 0.10018132453457879
Ocean volume                13.753889958402644
Percentage of ocean surface 10.96


In [9]:
# Set-up figure
def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    plt.show()
    return fig

def update_figure():
        plt.clf()
        ax1 = fig.add_subplot(121,projection='3d')

        # use equal x-y aspect with an explicit vertical exageration
        vert_exag = 4.
        ax1.set_xlim3d(0,max(NX,NY))
        ax1.set_ylim3d(0,max(NX,NY))
        ax1.set_zlim3d(0,ZMaxOrg)

        ax1.set_title('Surface Relief')

#        surf = ax1.plot_surface(X,Y,Z, cmap = cm.terrain, rstride=1, cstride=1,
#                antialiased=False,linewidth=0)

        ZPlot = np.copy(Z)
        ZPlot[ZPlot<ls.ZBeachLevel] = ls.ZBeachLevel 
        ZPlot -= ls.ZBeachLevel
        ax1.plot_surface(X,Y,ZPlot, cmap = cm.terrain, rstride=1, cstride=1,
                antialiased=False,linewidth=0)

        ax2 = fig.add_subplot(122,aspect='equal')
        ax2.set_title('Elevation')

        #im = ax2.pcolor(Z,cmap=cm.terrain)
        im = ax2.pcolor(ZPlot,cmap=cm.coolwarm)
        cs = ax2.contour(ZPlot,6,colors='k')

        # Add a color bar which maps values to colors.
        cbar = fig.colorbar(im, shrink=0.5, aspect=5)
        # Add the contour line levels to the colorbar
        cbar.add_lines(cs)

        #plt.show()
        plt.draw()
        plt.pause(0.0001)

In [10]:
# Set up figure
fig = init_figure()
update_figure()
Znew = np.copy(Z)

metadata = dict(title='Homework Ocean Erosion', artist='Matplotlib',comment='Wakanda forever.')
writer = FFMpegWriter(fps=15, metadata=metadata)

with writer.saving(fig, "fill.mp4", dpi=200):
    for it in range(1,n_iter):

        ls.calculate_collection_area(Z,NX,NY)
        ls.A *= dx*dy

        for i in range(NX):
            iL = np.mod(i-1,NX) # normally i-1 but observe p.b.c.
            iR = np.mod(i+1,NX) # normally i+1 but observe p.b.c.

            for j in range(NY):
                jD = np.mod(j-1,NY) # normally j-1 but observe p.b.c.
                jU = np.mod(j+1,NY) # normally j+1 but observe p.b.c.

                if ls.ocean[i,j]>0:
                    Psi_z  = 0;
                    Phi_z  = 0;
                else:
                    if ls.drain[i,j]>0: #this cell is a drain
                        s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                        s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                        s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                        s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                        gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)            

                    elif ls.drainage[i,j]>0: #this cell is a drainage point (it drains a pool)

                        if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                            gradient = (Z[i,j]-Z[iR,j])/dx #pool is on my left, I drain to the right, use this gradiant
                        elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[iL,j])/dx
                        elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jU])/dy
                        elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jD])/dy
                        else:
                            gradient = 0.02 # ??? This does happen (maybe when two pools merge)
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)

                    else: #this cell is a pool, assume it has some mass diffusion but no erosion!
                        Psi_z = 0.

                    if (Psi_z<0):
                        Psi_z = 0. 

                    # diffusion term
                    Phi_z = D * ( (Z[iR,j] - 2.*Z[i,j] + Z[iL,j]) / dx**2 \
                                + (Z[i,jU] - 2.*Z[i,j] + Z[i,jD]) / dx**2 )

                Znew[i,j] = Z[i,j] + (Phi_z - Psi_z + uplift )*dt  

                dZdt= (Znew[i,j] - Z[i,j]) / dt
                CFL = abs(dZdt) * dt / min(dx,dy)
                if (CFL>1.0):
                    print('\nWarning: Time step of',dt,'is probably too large. Safer would be:',dt/CFL)

                if (Znew[i,j]<0.):
                    Znew[i,j] = 0. # yes, this does happen at the boundary when kept at zero

        #Znew[0,:] = 0.0 # resets front boundary to 0
        Z = np.copy(Znew)

        ls.pool_check(Z,NX,NY)
        writer.grab_frame()
        
        if (np.mod(it,10)==0): 
            print(it,end='')
            update_figure()
            print(' Ocean level=',ls.ZBeachLevel,' Ocean surface fraction=',100*ls.AOcean/(NX*NY));
        else:
            print('.',end='')

    update_figure()
    print(' Simulation finished.')


.........10 Ocean level= 0.10121995491142899  Ocean surface fraction= 11.08
.........20 Ocean level= 0.09995050974560343  Ocean surface fraction= 12.28
......... Simulation finished.


In [11]:
print(Z)
print(Z2)

RandomRavel = Z.flatten() * 2
PerlinRavel = Z2.flatten()

print(RandomRavel.shape)
print(PerlinRavel.shape)

plt.clf()
plt.hist(RandomRavel, ec="black")
plt.title("Random Noise Height Distribution After 30 Erosion Cycles (Scaled)")
plt.xlim(0, 1)
plt.show()

# plt.clf()
# plt.title("Perlin Noise Height Distribution")
# plt.hist(PerlinRavel, ec="black")
# plt.show()

[[0.27646324 0.2359446  0.19085371 ... 0.24052132 0.27776503 0.29124126]
 [0.31746176 0.25508606 0.17072435 ... 0.24047511 0.31139581 0.33715968]
 [0.34357896 0.2501054  0.02790319 ... 0.23855116 0.33224944 0.36652431]
 ...
 [0.09763218 0.09406145 0.10563181 ... 0.24661492 0.13759303 0.01188838]
 [0.11937545 0.04660964 0.12726084 ... 0.22082287 0.08290843 0.11146627]
 [0.20644767 0.17402219 0.17286249 ... 0.23835801 0.21340186 0.2160128 ]]
[[0.52514288 0.63703496 0.76838913 ... 0.83412763 0.70127103 0.57817109]
 [0.52513822 0.63658825 0.76644386 ... 0.82349797 0.69486797 0.57568422]
 [0.52511977 0.63482213 0.75875288 ... 0.78147175 0.66955231 0.56585195]
 ...
 [0.26463392 0.29188184 0.35290269 ... 0.25375284 0.3516662  0.44238905]
 [0.33326286 0.35270735 0.40978637 ... 0.19285109 0.31498034 0.42814073]
 [0.42553268 0.44088065 0.49261864 ... 0.16828411 0.30018175 0.42239315]]
(2500,)
(2500,)
